## Setup...

In [1]:
# Various setup, probably mostly unused

from env import TestEnv
import pandas as pd
import json
import os
from conf import LisaLogging
from bart.common.Utils import area_under_curve
from trappy.plotter import plot_trace
from IPython.display import display
from trappy import ILinePlot
from trappy.stats.grammar import Parser
from bart.sched.SchedMultiAssert import SchedMultiAssert
import pandas as pd
from trace import Trace
LisaLogging.setup()
import logging
logging.getLogger('Trace').setLevel(logging.ERROR)
logging.getLogger('Analysis').setLevel(logging.WARNING)
logging.getLogger('EnergyMeter').setLevel(logging.DEBUG)
%matplotlib inline
from platforms.juno_energy import juno_energy
from platforms.pixel_energy import pixel_energy
import tests.eas.generic
from tests.eas.generic import EnergyModelTest
import numpy as np
from IPython.display import display
from wlgen import RTA, Periodic
from executor import Executor
from platforms.hikey_energy import hikey_energy
import numpy as np

2017-02-08 15:37:31,029 INFO    : root         : Using LISA logging configuration:
2017-02-08 15:37:31,030 INFO    : root         :   /home/brejac01/sources/lisa/logging.conf


In [2]:
# Some nonsense to get caiman to work on Brendan's computer
p = os.getenv('PATH').split(':')
caiman_path = '/opt/ds5_v5.23.0/bin'
if caiman_path not in p:
    p.insert(0, caiman_path)
    os.environ['PATH'] = ':'.join(p)

In [3]:
te = TestEnv(test_conf={
        'modules': ['cgroups'], 
        'ftrace': {
            'events': ['sched_switch', 'cpu_frequency', 'cpu_idle', 'sched_load_avg_cpu', 'sched_load_avg_task', 'irq*']
        }
    }, force_new=True)

2017-02-08 15:37:31,082 INFO    : TestEnv      : Using base path: /home/brejac01/sources/lisa
2017-02-08 15:37:31,083 INFO    : TestEnv      : Loading default (file) target configuration
2017-02-08 15:37:31,083 INFO    : TestEnv      : Loading target configuration [/home/brejac01/sources/lisa/target.config]...
2017-02-08 15:37:31,085 INFO    : TestEnv      : Loading custom (inline) test configuration
2017-02-08 15:37:31,086 INFO    : TestEnv      : External tools using:
2017-02-08 15:37:31,087 INFO    : TestEnv      :    ANDROID_HOME: /work/android-sdk-linux
2017-02-08 15:37:31,087 INFO    : TestEnv      :    CATAPULT_HOME: /home/brejac01/sources/lisa/tools/catapult
2017-02-08 15:37:31,088 INFO    : TestEnv      : Devlib modules to load: ['cpuidle', 'cgroups', 'cpufreq']
2017-02-08 15:37:31,088 INFO    : TestEnv      : Connecting Android target [04D314DF000BC57F]
2017-02-08 15:37:31,089 INFO    : TestEnv      : Connection settings:
2017-02-08 15:37:31,089 INFO    : TestEnv      :    {'

In [4]:
# Some nonsense to make LISA treat HiKey with the respect it deserves
from trappy.stats.Topology import Topology
hikey_topology = Topology(clusters=[[0, 1, 2, 3], [4, 5, 6, 7]])
te.topology = hikey_topology
te.platform['clusters'] = {'big': [0, 1, 2, 3], 'little': [4, 5, 6, 7]}

# Define Workloads
We're going to create two workloads with a handful of small tasks, such that they could fit onto a single cluster at the lowest OPP. 

To avoid evertying being thrown out by the periodiciy of the tasks, the start times and periods of the tasks are staggered.

We'll run this same workload both with and without using taskset to force them onto a single cluster.

In [5]:
def get_wloads(nrg_model, cpu=0, task_pct=4):
    cpu_node = nrg_model.cpu_nodes[cpu]
    cluster_node = cpu_node.parent
    ncpus = len(cluster_node.cpus)
    min_cap = cpu_node.min_capacity
    task_cap = int(1024 * (task_pct / 100.))
    tasks_per_cpu = int(min_cap / task_cap)
    ntasks = tasks_per_cpu * ncpus

    # Stagger the workloads so that they prevent shared idle states
    period_s = 10e-3
    stagger_s = 0.7e-3
    delays = np.arange(period_s, step=stagger_s)
    
    if len(delays) > ntasks:
        print "WARNING: not enough tasks to cover period with wakeups"
    
    tasks = {}
    for i in range(ntasks):
        tasks['{}pct_{}'.format(task_pct, i)] = {
            'kind': 'Periodic',
            'params': {
                'duty_cycle_pct': task_pct,
                'period_ms' : period_s * 1e3 + (i - (ntasks / 2)),
                'delay_s' : delays[i % len(delays)],
                'duration_s': 2
            }
        }
    
    wloads = {
        'forced_pack': {
            'type': 'rt-app',
            'conf': {
                'class': 'profile',
                'params': tasks,
                'cpus': [0, 1, 2, 3]
            }
        },
        'any_cpu': {
            'type': 'rt-app',
            'conf': {
                'class': 'profile',
                'params': tasks,
            }
        }
    }
        
    return wloads

In [6]:
wloads = get_wloads(hikey_energy)

# Run workloads
Now we'll run the workloads with the powersave governor

In [9]:
poor_mans_powersave = { # No powersave governor in hikey_defconfig
    'governor': 'userspace',
    'freqs':{
        0: 208000,
    }
}
performance = {
    'governor': 'performance'
}
executor = Executor(te, {
        'confs': [{
                'tag': 'myconf',
                'flags': ['ftrace', 'freeze_userspace'],
                'cpufreq': poor_mans_powersave,
            }],
        'wloads': wloads,
        'iterations': 15
    })

2017-02-08 15:37:57,230 INFO    : Executor     : Loading custom (inline) test configuration
2017-02-08 15:37:57,232 INFO    : Executor     : 
2017-02-08 15:37:57,233 INFO    : Executor     : ################################################################################
2017-02-08 15:37:57,234 INFO    : Executor     : Experiments configuration
2017-02-08 15:37:57,236 INFO    : Executor     : ################################################################################
2017-02-08 15:37:57,237 INFO    : Executor     : Configured to run:
2017-02-08 15:37:57,238 INFO    : Executor     :      1 target configurations:
2017-02-08 15:37:57,239 INFO    : Executor     :       myconf
2017-02-08 15:37:57,240 INFO    : Executor     :      2 workloads (15 iterations each)
2017-02-08 15:37:57,242 INFO    : Executor     :       any_cpu, forced_pack
2017-02-08 15:37:57,243 INFO    : Executor     : Total: 30 experiments
2017-02-08 15:37:57,244 INFO    : Executor     : Results will be collected under

In [10]:
executor.run()

2017-02-08 15:37:57,253 INFO    : Executor     : 
2017-02-08 15:37:57,255 INFO    : Executor     : ################################################################################
2017-02-08 15:37:57,256 INFO    : Executor     : Experiments execution
2017-02-08 15:37:57,257 INFO    : Executor     : ################################################################################
2017-02-08 15:37:57,258 INFO    : Executor     : 
2017-02-08 15:37:57,259 INFO    : Executor     : ================================================================================
2017-02-08 15:37:57,260 INFO    : Executor     : configuring target for [myconf] experiments
2017-02-08 15:37:57,589 WARNING : Executor     : Setting target SELinux in permissive mode
2017-02-08 15:37:57,764 INFO    : Executor     : Configuring all CPUs to use [userspace] cpufreq governor
2017-02-08 15:37:57,930 INFO    : Executor     :        CPUFreq - CPU frequencies: {0: 208000}
2017-02-08 15:37:58,390 INFO    : Workload     : Setup

2017-02-08 15:38:36,094 DEBUG   : EnergyMeter  : RESET: []
2017-02-08 15:38:36,103 INFO    : Workload     : Workload execution START:
2017-02-08 15:38:36,106 INFO    : Workload     :    /data/local/tmp/bin/rt-app /data/local/tmp/devlib-target/run_dir/any_cpu_00.json 2>&1
2017-02-08 15:38:39,735 DEBUG   : EnergyMeter  : Energy [             BAT]: 0.022079
2017-02-08 15:39:00,560 INFO    : Executor     : Collected FTrace binary trace:
2017-02-08 15:39:00,562 INFO    : Executor     :    <res_dir>/rtapp:myconf:any_cpu/1/trace.dat
2017-02-08 15:39:00,564 INFO    : Executor     : Collected FTrace function profiling:
2017-02-08 15:39:00,565 INFO    : Executor     :    <res_dir>/rtapp:myconf:any_cpu/1/trace_stat.json
2017-02-08 15:39:00,566 INFO    : Executor     : Un-freezing userspace tasks
2017-02-08 15:39:03,984 INFO    : Executor     : Calling postrun step
2017-02-08 15:39:12,821 INFO    : Executor     : --------------------------------------------------------------------------------
2017

2017-02-08 15:39:47,921 DEBUG   : EnergyMeter  : RESET: []
2017-02-08 15:39:47,932 INFO    : Workload     : Workload execution START:
2017-02-08 15:39:47,933 INFO    : Workload     :    /data/local/tmp/bin/rt-app /data/local/tmp/devlib-target/run_dir/any_cpu_00.json 2>&1
2017-02-08 15:39:51,550 DEBUG   : EnergyMeter  : Energy [             BAT]: 0.021034
2017-02-08 15:40:12,594 INFO    : Executor     : Collected FTrace binary trace:
2017-02-08 15:40:12,596 INFO    : Executor     :    <res_dir>/rtapp:myconf:any_cpu/2/trace.dat
2017-02-08 15:40:12,597 INFO    : Executor     : Collected FTrace function profiling:
2017-02-08 15:40:12,599 INFO    : Executor     :    <res_dir>/rtapp:myconf:any_cpu/2/trace_stat.json
2017-02-08 15:40:12,600 INFO    : Executor     : Un-freezing userspace tasks
2017-02-08 15:40:16,138 INFO    : Executor     : --------------------------------------------------------------------------------
2017-02-08 15:40:16,140 INFO    : Executor     : ~~~~~~~~~~~~~~~~~~~~~~~~~

2017-02-08 15:40:51,543 DEBUG   : EnergyMeter  : RESET: []
2017-02-08 15:40:51,553 INFO    : Workload     : Workload execution START:
2017-02-08 15:40:51,556 INFO    : Workload     :    /data/local/tmp/bin/rt-app /data/local/tmp/devlib-target/run_dir/any_cpu_00.json 2>&1
2017-02-08 15:40:55,227 DEBUG   : EnergyMeter  : Energy [             BAT]: 0.021221
2017-02-08 15:41:16,245 INFO    : Executor     : Collected FTrace binary trace:
2017-02-08 15:41:16,247 INFO    : Executor     :    <res_dir>/rtapp:myconf:any_cpu/3/trace.dat
2017-02-08 15:41:16,249 INFO    : Executor     : Collected FTrace function profiling:
2017-02-08 15:41:16,250 INFO    : Executor     :    <res_dir>/rtapp:myconf:any_cpu/3/trace_stat.json
2017-02-08 15:41:16,251 INFO    : Executor     : Un-freezing userspace tasks
2017-02-08 15:41:19,686 INFO    : Executor     : --------------------------------------------------------------------------------
2017-02-08 15:41:19,688 INFO    : Executor     : ~~~~~~~~~~~~~~~~~~~~~~~~~

2017-02-08 15:41:54,865 DEBUG   : EnergyMeter  : RESET: []
2017-02-08 15:41:54,873 INFO    : Workload     : Workload execution START:
2017-02-08 15:41:54,875 INFO    : Workload     :    /data/local/tmp/bin/rt-app /data/local/tmp/devlib-target/run_dir/any_cpu_00.json 2>&1
2017-02-08 15:41:58,493 DEBUG   : EnergyMeter  : Energy [             BAT]: 0.022156
2017-02-08 15:42:20,101 INFO    : Executor     : Collected FTrace binary trace:
2017-02-08 15:42:20,103 INFO    : Executor     :    <res_dir>/rtapp:myconf:any_cpu/4/trace.dat
2017-02-08 15:42:20,105 INFO    : Executor     : Collected FTrace function profiling:
2017-02-08 15:42:20,106 INFO    : Executor     :    <res_dir>/rtapp:myconf:any_cpu/4/trace_stat.json
2017-02-08 15:42:20,107 INFO    : Executor     : Un-freezing userspace tasks
2017-02-08 15:42:23,779 INFO    : Executor     : --------------------------------------------------------------------------------
2017-02-08 15:42:23,781 INFO    : Executor     : ~~~~~~~~~~~~~~~~~~~~~~~~~

...

2017-02-08 16:05:21,661 DEBUG   : EnergyMeter  : RESET: []
2017-02-08 16:05:21,671 INFO    : Workload     : Workload execution START:
2017-02-08 16:05:21,673 INFO    : Workload     :    /data/local/tmp/bin/taskset 0xF /data/local/tmp/bin/rt-app /data/local/tmp/devlib-target/run_dir/forced_pack_00.json 2>&1
2017-02-08 16:05:25,347 DEBUG   : EnergyMeter  : Energy [             BAT]: 0.021261
2017-02-08 16:05:46,228 INFO    : Executor     : Collected FTrace binary trace:
2017-02-08 16:05:46,230 INFO    : Executor     :    <res_dir>/rtapp:myconf:forced_pack/11/trace.dat
2017-02-08 16:05:46,231 INFO    : Executor     : Collected FTrace function profiling:
2017-02-08 16:05:46,232 INFO    : Executor     :    <res_dir>/rtapp:myconf:forced_pack/11/trace_stat.json
2017-02-08 16:05:46,233 INFO    : Executor     : Un-freezing userspace tasks
2017-02-08 16:05:49,816 INFO    : Executor     : --------------------------------------------------------------------------------
2017-02-08 16:05:49,818 INFO

2017-02-08 16:06:25,515 DEBUG   : EnergyMeter  : RESET: []
2017-02-08 16:06:25,526 INFO    : Workload     : Workload execution START:
2017-02-08 16:06:25,528 INFO    : Workload     :    /data/local/tmp/bin/taskset 0xF /data/local/tmp/bin/rt-app /data/local/tmp/devlib-target/run_dir/forced_pack_00.json 2>&1
2017-02-08 16:06:29,178 DEBUG   : EnergyMeter  : Energy [             BAT]: 0.021143
2017-02-08 16:06:50,376 INFO    : Executor     : Collected FTrace binary trace:
2017-02-08 16:06:50,378 INFO    : Executor     :    <res_dir>/rtapp:myconf:forced_pack/12/trace.dat
2017-02-08 16:06:50,379 INFO    : Executor     : Collected FTrace function profiling:
2017-02-08 16:06:50,380 INFO    : Executor     :    <res_dir>/rtapp:myconf:forced_pack/12/trace_stat.json
2017-02-08 16:06:50,382 INFO    : Executor     : Un-freezing userspace tasks
2017-02-08 16:06:53,820 INFO    : Executor     : --------------------------------------------------------------------------------
2017-02-08 16:06:53,822 INFO

2017-02-08 16:07:28,856 DEBUG   : EnergyMeter  : RESET: []
2017-02-08 16:07:28,866 INFO    : Workload     : Workload execution START:
2017-02-08 16:07:28,868 INFO    : Workload     :    /data/local/tmp/bin/taskset 0xF /data/local/tmp/bin/rt-app /data/local/tmp/devlib-target/run_dir/forced_pack_00.json 2>&1
2017-02-08 16:07:32,531 DEBUG   : EnergyMeter  : Energy [             BAT]: 0.021151
2017-02-08 16:07:53,277 INFO    : Executor     : Collected FTrace binary trace:
2017-02-08 16:07:53,279 INFO    : Executor     :    <res_dir>/rtapp:myconf:forced_pack/13/trace.dat
2017-02-08 16:07:53,280 INFO    : Executor     : Collected FTrace function profiling:
2017-02-08 16:07:53,281 INFO    : Executor     :    <res_dir>/rtapp:myconf:forced_pack/13/trace_stat.json
2017-02-08 16:07:53,282 INFO    : Executor     : Un-freezing userspace tasks
2017-02-08 16:07:56,758 INFO    : Executor     : --------------------------------------------------------------------------------
2017-02-08 16:07:56,760 INFO

2017-02-08 16:08:31,948 DEBUG   : EnergyMeter  : RESET: []
2017-02-08 16:08:31,959 INFO    : Workload     : Workload execution START:
2017-02-08 16:08:31,961 INFO    : Workload     :    /data/local/tmp/bin/taskset 0xF /data/local/tmp/bin/rt-app /data/local/tmp/devlib-target/run_dir/forced_pack_00.json 2>&1
2017-02-08 16:08:35,637 DEBUG   : EnergyMeter  : Energy [             BAT]: 0.020973
2017-02-08 16:08:56,690 INFO    : Executor     : Collected FTrace binary trace:
2017-02-08 16:08:56,692 INFO    : Executor     :    <res_dir>/rtapp:myconf:forced_pack/14/trace.dat
2017-02-08 16:08:56,694 INFO    : Executor     : Collected FTrace function profiling:
2017-02-08 16:08:56,695 INFO    : Executor     :    <res_dir>/rtapp:myconf:forced_pack/14/trace_stat.json
2017-02-08 16:08:56,696 INFO    : Executor     : Un-freezing userspace tasks
2017-02-08 16:09:00,143 INFO    : Executor     : --------------------------------------------------------------------------------
2017-02-08 16:09:00,145 INFO

2017-02-08 16:09:35,228 DEBUG   : EnergyMeter  : RESET: []
2017-02-08 16:09:35,240 INFO    : Workload     : Workload execution START:
2017-02-08 16:09:35,242 INFO    : Workload     :    /data/local/tmp/bin/taskset 0xF /data/local/tmp/bin/rt-app /data/local/tmp/devlib-target/run_dir/forced_pack_00.json 2>&1
2017-02-08 16:09:38,866 DEBUG   : EnergyMeter  : Energy [             BAT]: 0.021524
2017-02-08 16:09:59,919 INFO    : Executor     : Collected FTrace binary trace:
2017-02-08 16:09:59,921 INFO    : Executor     :    <res_dir>/rtapp:myconf:forced_pack/15/trace.dat
2017-02-08 16:09:59,922 INFO    : Executor     : Collected FTrace function profiling:
2017-02-08 16:09:59,924 INFO    : Executor     :    <res_dir>/rtapp:myconf:forced_pack/15/trace_stat.json
2017-02-08 16:09:59,925 INFO    : Executor     : Un-freezing userspace tasks
2017-02-08 16:10:03,630 INFO    : Executor     : --------------------------------------------------------------------------------
2017-02-08 16:10:03,632 INFO

# Examine Results

In [11]:
traces = [Trace(te.platform, e.out_dir, ['sched_switch', 'cpu_idle', 'cpu_frequency']) for e in executor.experiments]

## Plot task residency
It's worth visually inspecting the task residency to check that the "un-packed" runs were really unpacked and that there aren't any aliasing problems that would obviously make un-packed runs just as efficient as packed runs

In [12]:
for trace in traces:
    plot_trace(trace.ftrace)

In [13]:
# Plot cluster active-time. This shouldn't be needed, I used this to figure out when the 
# workload was really stressing both clusters where it wasn't packed (i.e. whether idle periods were aligned)
if False:
    clusters = [[0, 1, 2, 3], [4, 5, 6, 7]]
    for trace in traces:
        ca_signals = []
        for cluster in clusters:
            ca_signals.append(pd.DataFrame(trace.getClusterActiveSignal(cluster)))
        ILinePlot(ca_signals, column=0, drawstyle='steps-post', fill=True, fill_alpha=0.8).view() 
        trace.analysis.idle.plotClusterIdleStateResidency()

# Compare energy usage between packed an unpacked runs

Split up workload runs between those that were packed onto a single cluster and those that weren't. Then compare the mean energy usage for those two classes of workload runs.

In [14]:
def examine_experiment(experiment):
    trace = Trace(te.platform, experiment.out_dir, ['sched_switch'])
    ma = SchedMultiAssert(trace.ftrace, hikey_topology, experiment.wload.tasks.keys())
    cluster_conclusions = []
    for cluster in te.topology.get_level('cluster'):
        residencies = [t['residency'] for p, t in ma.getResidency('cluster', cluster, percent=True).iteritems()]
        if all(r > 90 for r in residencies):
            cluster_conclusions.append('PACKED')
        else:
            cluster_conclusions.append(None)
    packed = [i for i, c in enumerate(cluster_conclusions) if c == 'PACKED']
    with open(os.path.join(experiment.out_dir, 'energy.json')) as f:
        energy = json.load(f)
        energy = energy['BAT']
    if not packed:
        print "I don't think we packed onto any cluster"
        return False, energy
        # plot_trace(trace.ftrace)
    elif len(packed) == 1:
        [i] = packed
        print 'I think we packed onto cluster {} ({})'.format(i, te.topology.get_node('cluster', i))
        return True, energy
    else:
        raise Exception('i am borken')

In [15]:
previous_energy_records = [[], []] # Use this to store old results

In [16]:
energy_records = previous_energy_records
for experiment in executor.experiments:
    packed, energy = examine_experiment(experiment)
    energy_records[packed].append(energy)

I don't think we packed onto any cluster
I think we packed onto cluster 0 ([0, 1, 2, 3])
I think we packed onto cluster 0 ([0, 1, 2, 3])
I don't think we packed onto any cluster
I don't think we packed onto any cluster
I don't think we packed onto any cluster
I don't think we packed onto any cluster
I don't think we packed onto any cluster
I don't think we packed onto any cluster
I don't think we packed onto any cluster
I don't think we packed onto any cluster
I don't think we packed onto any cluster
I think we packed onto cluster 0 ([0, 1, 2, 3])
I don't think we packed onto any cluster
I don't think we packed onto any cluster
I think we packed onto cluster 0 ([0, 1, 2, 3])
I think we packed onto cluster 0 ([0, 1, 2, 3])
I think we packed onto cluster 0 ([0, 1, 2, 3])
I think we packed onto cluster 0 ([0, 1, 2, 3])
I think we packed onto cluster 0 ([0, 1, 2, 3])
I think we packed onto cluster 0 ([0, 1, 2, 3])
I think we packed onto cluster 0 ([0, 1, 2, 3])
I think we packed onto clust

In [17]:
unpacked_nrg, packed_nrg = [np.mean(n) for n in energy_records]
print 'Average energy when not packed: {}'.format(unpacked_nrg)
print 'Average energy when packed: {}'.format(packed_nrg)

print 'Improvement by packing: {:02f}%'.format(((unpacked_nrg - packed_nrg) / unpacked_nrg) * 100)

Average energy when not packed: 0.0224648421634
Average energy when packed: 0.0212262674265
Improvement by packing: 5.513392%
